### Read data into PySpark Dataframe.

In [0]:
!pip install matplotlib
!pip install seaborn 
!pip install --upgrade pip 

You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-621872c6-e4a8-4595-8635-7402a2bdce7a/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-621872c6-e4a8-4595-8635-7402a2bdce7a/bin/python -m pip install --upgrade pip' command.
     |████████████████████████████████| 2.1 MB 16.7 MB/s 
  Attempting uninstall: pip
    Found existing installation: pip 21.2.4
    Uninstalling pip-21.2.4:
      Successfully uninstalled pip-21.2.4


In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.sql.window import Window
from pyspark.sql.types import *
import matplotlib.pyplot as plt
import base64
import pyspark
from pyspark.sql import functions as F
import seaborn as sns
from pyspark.sql import SparkSession
import spacy
import numpy as np
from pyspark.sql.functions import col, concat
spark = SparkSession.builder.getOrCreate()

In [0]:
profiles = spark.read.parquet('/linkedin/people')

In [0]:
companies = spark.read.parquet('/linkedin/companies')

## Extracting Past Jobs

In [0]:
# check if 'experience' is not empty, 'id' is not null or empty, and 'name' is not null or empty

profiles_df = profiles.filter((size(profiles['experience']) > 0)&(col('id').isNotNull()) & (col('id') != '') &
                                    (col('name').isNotNull()) & (col('name') != '')).withColumn('exp_length',size(profiles['experience']))

# create a new column 'exp_length' with the size of 'experience'
profiles_df = profiles_df.withColumn('exp',explode(profiles['experience']))

# explode the 'experience' column to create a new row for each experience entry
profiles_df = profiles_df.select(profiles_df['id'].alias('user_id'),profiles_df['name'].alias('user_name'),profiles_df['current_company:company_id'].alias('current_company_id'),
                             profiles_df['current_company:name'].alias('current_company_name'),profiles_df['position'].alias('current_position'),'exp.subtitle','exp_length','url').groupBy("user_id", "user_name",'url','current_company_id','current_company_name','current_position','exp_length').agg(
    countDistinct(col("subtitle")).alias("distinct_company_count")).orderBy(col("exp_length").desc(),col("user_id").desc())

result = profiles_df.select('user_id','user_name','url','current_company_id','current_company_name','current_position',
                            'distinct_company_count')

In [0]:
final_result = profiles_df.withColumn('combined', concat(col('current_position'), lit(" "), col('current_company_name')))
display(final_result)

user_id user_name url current_company_id current_company_name current_position exp_length distinct_company_count combined cheretheriot Chere Theriot https://www.linkedin.com/in/cheretheriot null Film, Television, Commercial, Print Set Decoration, Art Direction, Production Design, Props 97 77 Set Decoration, Art Direction, Production Design, Props Film, Television, Commercial, Print amelia-ferroni-09b02310 Amelia Ferroni https://www.linkedin.com/in/amelia-ferroni-09b02310 null Self-employed Freelance - Script Supervisor 95 69 Freelance - Script Supervisor Self-employed jessicafeiyali Jessica Li https://www.linkedin.com/in/jessicafeiyali beacons-ai Beacons Chief of Staff at Beacons (YC S19) | Harvard Alum 94 90 Chief of Staff at Beacons (YC S19) | Harvard Alum Beacons brettcarlson4 Brett Carlson https://www.linkedin.com/in/brettcarlson4 null null Commercial Line Producer and Production Manager 90 53 null jchengvc J C. https://www.linkedin.com/in/jchengvc?_l=en_us gen1capital Gen 1 Capital Venture Capital Investor, Entrepreneur 84 83 Venture Capital Investor, Entrepreneur Gen 1 Capital derekmccants Derek McCants, ACE https://www.linkedin.com/in/derekmccants?_l=en_us null American Cinema Editors null 80 75 null allyn-nielsen-4755666a Allyn Nielsen https://www.linkedin.com/in/allyn-nielsen-4755666a null self retired at self 79 1 retired at self self aliciagood Alicia Good https://www.linkedin.com/in/aliciagood pitman-casting PITMAN CASTING Casting Director at Damn Good Casting 79 58 Casting Director at Damn Good Casting PITMAN CASTING patriciafarrell Patricia Farrell https://www.linkedin.com/in/patriciafarrell null Billy Graham Rapid Response Team Member at John Maxwell Team 72 48 Member at John Maxwell Team Billy Graham Rapid Response Team jyoti-singh-171172a Jyoti Singh https://www.linkedin.com/in/jyoti-singh-171172a null RVP Productions Zindagi Hain 72 69 Zindagi Hain RVP Productions imanilindsey imani L. https://www.linkedin.com/in/imanilindsey null MERE IMANI executive producer at mere studios 66 47 executive producer at mere studios MERE IMANI alimcgee Ali McGee https://www.linkedin.com/in/alimcgee mcp-presents MCP Presents Event Operations & Project Management 64 41 Event Operations & Project Management MCP Presents cgoetzus Christopher Goetz https://www.linkedin.com/in/cgoetzus null Kingston Systems Drilling Rig Inspection & Commissioning, Intake, Expert Witness, Troubleshooting, FMECA. BOP, DP, Cybersecurity, Controls, Expert Facilitator of FMEAs DWOPs, and more. since 2007 63 46 Drilling Rig Inspection & Commissioning, Intake, Expert Witness, Troubleshooting, FMECA. BOP, DP, Cybersecurity, Controls, Expert Facilitator of FMEAs DWOPs, and more. since 2007 Kingston Systems alanaspears Alana Spears https://www.linkedin.com/in/alanaspears insight-global Insight Global Nike Global Brand Creative Studio Manager 63 27 Nike Global Brand Creative Studio Manager Insight Global chinge Everett Ching https://www.linkedin.com/in/chinge crunchyroll Crunchyroll Freelance Creative @ Crunchyroll • CD / AD • Mentor 62 47 Freelance Creative @ Crunchyroll • CD / AD • Mentor Crunchyroll brit-whittle-6267a016 Brit Whittle https://www.linkedin.com/in/brit-whittle-6267a016 null Prestige Management Group Professional Actor and Voice Over Artist 62 48 Professional Actor and Voice Over Artist Prestige Management Group tonycarlson Tony Carlson https://www.linkedin.com/in/tonycarlson riot-games Riot Games Senior Motion Designer • Freelance 61 41 Senior Motion Designer • Freelance Riot Games robert-john-malone-403024a Robert John Malone https://www.linkedin.com/in/robert-john-malone-403024a null Sacred Sound Services Sacred Sound Services 61 52 Sacred Sound Services Sacred Sound Services johnbeach John Beach https://www.linkedin.com/in/johnbeach?_l=en_us indigo-films Indigo Films Happy to be alive, loving, and being loved. 61 51 Happy to be alive, loving, and being loved. Indigo Films caitlin-noah-a8707192 Caitlin Noah https://www.linkedin.com/in/caitl